In [13]:
import os
import json
import cv2
import random

# Function to plot one bounding box on the image
def plot_one_box(c1, c2, img, color=None, label=None, line_thickness=3):
    tl = line_thickness or round(0.002 * (img.shape[0] + img.shape[1]) / 2) + 1  # line/font thickness
    color = color or [random.randint(0, 255) for _ in range(3)]
    cv2.rectangle(img, c1, c2, color, thickness=1, lineType=cv2.LINE_AA)
    if label:
        tf = max(tl - 1, 1)  # font thickness
        t_size = cv2.getTextSize(label, 0, fontScale=tl / 3, thickness=tf)[0]
        c2 = c1[0] + t_size[0], c1[1] - t_size[1] - 3
        cv2.rectangle(img, c1, c2, color, -1, cv2.LINE_AA)  # filled
        cv2.putText(img, label, (c1[0], c1[1] - 2), 0, tl / 3, [225, 255, 255], thickness=tf, lineType=cv2.LINE_AA)


# Create the labels directory if it does not exist
os.makedirs(label_directory, exist_ok=True)

# Your custom labels
custom_labels = ['Person', 'Car', 'Truck', 'Bus', 'Bicycle', 'Bike', 'Extra_vehicle', 'Dog']

# Create a mapping between FLIR ADAS and your custom labels
label_mapping = {
    'Person': 'Person',
    'Car': 'Car',
    'Truck': 'Truck',
    'Bus': 'Bus',
    'Bike': 'Bicycle',
    'Motorcycle': 'Bike',
    'Scooter': 'Bike',
    'Other Vehicle': 'Extra_vehicle',
    'Train': 'Extra_vehicle',
    'Skateboard': None,
    'Stroller': None,
    'Dog': 'Dog',
    # Skip these labels
    'Traffic light': None,
    'Fire Hydrant': None,
    'Street Sign': None
}

# Process images and annotations
def process_images_and_annotations(image_directory, base_dir, label_directory, custom_labels, label_mapping):
    count = 0
    image_names = []
    
    with open(os.path.join(base_dir, "index.json")) as f:
        data = json.load(f)
        frames = data['frames']
        width, height = 640.0, 512.0
        
        for frame in frames:
            # Build image name
            image_name = f"video-{frame['videoMetadata']['videoId']}-frame-{str(frame['videoMetadata']['frameIndex']).zfill(6)}-{frame['datasetFrameId']}.jpg"
            image_names.append(image_directory + image_name)
            count += 1
            
            # Read the image
            img = cv2.imread(os.path.join(base_dir, "data", image_name))
            if img is None:
                print(f"Image not found: {image_name}")
                continue
            
            converted_results = []

            # Debug: Check if there are any annotations for the image
            if not frame["annotations"]:
                print(f"No annotations for {image_name}")
                continue
            
            for anno in frame["annotations"]:
                flir_label = anno['labels'][0]  # Get the label from FLIR dataset
                print(f"Processing label {flir_label} for image {image_name}")

                # Map FLIR label to custom label and skip if it's not in custom_labels
                custom_label = label_mapping.get(flir_label)
                if custom_label is None:
                    print(f"Skipping label {flir_label} as it's not mapped to a custom label")
                    continue
                
                if custom_label in custom_labels:
                    bbox_height = anno["boundingBox"]["h"]
                    bbox_width = anno["boundingBox"]["w"]
                    x = anno["boundingBox"]["x"]
                    y = anno["boundingBox"]["y"]
                    cat_id = custom_labels.index(custom_label)

                    # YOLO format (x_center, y_center, width, height)
                    x_center, y_center = (x + bbox_width / 2, y + bbox_height / 2)
                    x_rel, y_rel = (x_center / width, y_center / height)
                    w_rel, h_rel = (bbox_width / width, bbox_height / height)
                    
                    # Debug: Print the converted annotation before adding it
                    print(f"Converted annotation for {custom_label}: {(cat_id, x_rel, y_rel, w_rel, h_rel)}")
                    
                    converted_results.append((cat_id, x_rel, y_rel, w_rel, h_rel))

                    # Draw bounding box for visualization
                    c1 = (x, y)
                    c2 = (x + bbox_width, y + bbox_height)
                    plot_one_box(c1, c2, img, label=custom_label)

            # Debug: Check if any annotations were converted
            if not converted_results:
                print(f"No annotations to save for {image_name}")
                continue

            # Save the labels in YOLO format to the specified label directory
            label_file_path = os.path.join(label_directory, str(image_name)[:-4] + '.txt')
            with open(label_file_path, 'w+') as file:
                file.write('\n'.join('%d %.6f %.6f %.6f %.6f' % res for res in converted_results))
            
            print(f"Saved labels for {image_name} to {label_file_path}")
        
        # Save all image names to a file
        with open(os.path.join(base_dir, 'all_image_names.txt'), 'w+') as file:
            file.write('\n'.join(image_names))
        print(f"Processed {count} images.")

# Call the function to process images and annotations, saving labels in the custom directory
process_images_and_annotations(image_directory, base_dir, label_directory, custom_labels, label_mapping)


Processing label light for image video-GzdKTLbkG5F7gAunM-frame-000108-QHZmA4QTZCnzBG3HZ.jpg
Skipping label light as it's not mapped to a custom label
Processing label light for image video-GzdKTLbkG5F7gAunM-frame-000108-QHZmA4QTZCnzBG3HZ.jpg
Skipping label light as it's not mapped to a custom label
Processing label light for image video-GzdKTLbkG5F7gAunM-frame-000108-QHZmA4QTZCnzBG3HZ.jpg
Skipping label light as it's not mapped to a custom label
Processing label light for image video-GzdKTLbkG5F7gAunM-frame-000108-QHZmA4QTZCnzBG3HZ.jpg
Skipping label light as it's not mapped to a custom label
Processing label sign for image video-GzdKTLbkG5F7gAunM-frame-000108-QHZmA4QTZCnzBG3HZ.jpg
Skipping label sign as it's not mapped to a custom label
Processing label sign for image video-GzdKTLbkG5F7gAunM-frame-000108-QHZmA4QTZCnzBG3HZ.jpg
Skipping label sign as it's not mapped to a custom label
Processing label sign for image video-GzdKTLbkG5F7gAunM-frame-000108-QHZmA4QTZCnzBG3HZ.jpg
Skipping labe

KeyboardInterrupt: 

In [11]:

image_directory = "/workspace/MLV_IR_OD/datasets/flir_adas/images_thermal_train/data"  # Path of images
base_dir = "/workspace/MLV_IR_OD/datasets/flir_adas/images_thermal_train"  # Path where index.json and other data are stored
label_directory = "/workspace/MLV_IR_OD/datasets/flir_adas/YOLOformat"